# Image Captioning

La idea de la práctica es desarrollar un modelo con redes neuronales que permita "subtitular" una imagen, describiendola.

Para ello usamos una arquitectura de encoder-decoder, es decir, cogemos una imagen, extraemos sus caracteristicas, y con la descripción que tenemos de la misma entrenamos una LSTM para extraer la descripción que tiene según las caracteristicas.

![imagen del modelo](https://raw.githubusercontent.com/yunjey/pytorch-tutorial/master/tutorials/03-advanced/image_captioning/png/model.png)


## Datos
Para entrenar la red neuronal usaremos los datos de [Flicker30K](http://shannon.cs.illinois.edu/DenotationGraph/data/index.html)

Para la ejecución de la practica este dataset es excesivo. De hecho, al intentar ejecutar los pasos con todo el dataset Google Colab ha llegado a pensar que estaba minando bitcoins y [ha límitado los recursos](https://research.google.com/colaboratory/faq.html#gpu-availability) (menos disco duro y sin GPU).

Así pues, considerando que el objetivo de la practica es más bien mostrar el camino y no conseguir unos resultados exactos, he preferido limitar el número de imagenes y de descripciones usadas para entrenar la red neuronal, así como disminuir el número de épocas usadas para entrenar la red.

Pese a todo he procurado dejar el código de tal manera que si tengo acceso a una máquina más potente (o estoy dispuesto a dejar mi ordenador entrenando la red varias semanas) poder generar un modelo más completo con el menor número posible de cambios.

Por ello, las partes computacionalmente ligeras las he realizado para las 30.000 imagenes del dataset, pero la parte del LSTM la he limitado.


In [0]:
#URLS de los datasets
ANNOTATIONS_URL = 'http://shannon.cs.illinois.edu/DenotationGraph/data/flickr30k.tar.gz'
IMAGES_URL_TRAIN = 'http://shannon.cs.illinois.edu/DenotationGraph/data/flickr30k-images.tar'

## Preparación de datos


### Descripciones

#### Descarga de descripciones

In [2]:
#descarga de descripciones
!wget http://shannon.cs.illinois.edu/DenotationGraph/data/flickr30k.tar.gz

--2019-08-29 01:00:54--  http://shannon.cs.illinois.edu/DenotationGraph/data/flickr30k.tar.gz
Resolving shannon.cs.illinois.edu (shannon.cs.illinois.edu)... 18.220.149.166
Connecting to shannon.cs.illinois.edu (shannon.cs.illinois.edu)|18.220.149.166|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 3652513 (3.5M) [application/x-gzip]
Saving to: ‘flickr30k.tar.gz.1’

flickr30k.tar.gz.1  100%[===================>]   3.48M  18.8MB/s    in 0.2s    

2019-08-29 01:00:54 (18.8 MB/s) - ‘flickr30k.tar.gz.1’ saved [3652513/3652513]



In [3]:
# Descomprimimos
!tar -xvzf flickr30k.tar.gz

readme.txt
results_20130124.token


#### Limpieza y preparación de descripciones 

Definimos dos funciones auxiliares que nos permiten leer y grabar documentos.

In [0]:
def load_doc(filename):
	# open the file as read only
	file = open(filename, 'r')
	# read all text
	text = file.read()
	# close the file
	file.close()
	return text

# save descriptions to file, one per line
def save_doc(descriptions, filename):
	lines = list()
	for key, desc in descriptions.items():
		lines.append(key + ' ' + desc)
	data = '\n'.join(lines)
	file = open(filename, 'w')
	file.write(data)
	file.close()

In [0]:
filename = 'results_20130124.token'
# Cargamos las descripciones
doc = load_doc(filename)

En doc tenemos:

```NOMBRE_DE_ARCHIVO.JPG```**#**```ID_DESC```**\t**````DESCRIPCION```

(Un mismo archivo puede tener varias descripciones)

In [6]:
doc[0:150]

'1000092795.jpg#0\tTwo young guys with shaggy hair look at their hands while hanging out in the yard .\n1000092795.jpg#1\tTwo young , White males are outs'

In [7]:
# Funcion para cargar las descripciones
def load_descriptions(doc):
  # creamos un diccionario que tiene como clave el nombre de archivo y como valor
  # la descripcion de la imagen
  mapping = dict()
  # Para cada linea
  for line in doc.split('\n'):
    #separar la linea por espacios
    tokens = line.split()
    if len(line) < 2:
      continue
      # la primera palabra es el image ID, el resto la descripción
    image_id, image_desc = tokens[0], tokens[1:]
		# quitar la extension .jpg del imageID
    image_id = image_id.split('.')[0]
		# Convertir la descripcion (en este momento una cadesna de tokens en una cadenba
    image_desc = ' '.join(image_desc)
		# guardar ña primera descripcion de cada imagen
    if image_id not in mapping:
      mapping[image_id] = image_desc
      
  return mapping
 
# parse descriptions
descriptions = load_descriptions(doc)
print('Loaded: %d ' % len(descriptions))

Loaded: 31783 


Para la realización de la practica, y teniendo en cuenta que sólo es una aproximación sólo me quedo con la `primera descripción. En el entrenamiento final, tendría que usar todas las descripciones, no sólo la primera.


In [8]:
import string

def clean_descriptions(descriptions):
  # palabras a minusculas, eliminamos palabras de una sola letra
  
	# prepare translation table for removing punctuation
	table = str.maketrans('', '', string.punctuation)
	for key, desc in descriptions.items():
		# tokenize
		desc = desc.split()
		# convert to lower case
		desc = [word.lower() for word in desc]
		# remove punctuation from each token
		desc = [w.translate(table) for w in desc]
		# remove hanging 's' and 'a'
		desc = [word for word in desc if len(word)>1]
		# store as string
		descriptions[key] =  ' '.join(desc)

# clean descriptions
clean_descriptions(descriptions)
# summarize vocabulary
all_tokens = ' '.join(descriptions.values()).split()
vocabulary = set(all_tokens)
print('Vocabulary Size: %d' % len(vocabulary))

Vocabulary Size: 13130


Una vez hecho todo esto grabamos las descripciones como un archivo de texto, para poder recurrir a él si reinicamos la máquina.
(Este archivo se incluye en el GIT)

In [0]:
save_doc(descriptions, 'descriptions.txt')  

En la variable descriptions nos ha quedado un diccionario con el nombre de archivo, y su descripción. Estos datos los usaremos para entrenar nuestro modelo LSTM

In [10]:
descriptions.keys()

dict_keys(['1000092795', '10002456', '1000268201', '1000344755', '1000366164', '1000523639', '1000919630', '10010052', '1001465944', '1001545525', '1001573224', '1001633352', '1001773457', '1001896054', '100197432', '100207720', '1002674143', '1003163366', '1003420127', '1003428081', '100444898', '1005216151', '100577935', '1006452823', '100652400', '1007129816', '100716317', '1007205537', '1007320043', '100759042', '10082347', '10082348', '100845130', '10090841', '1009434119', '1009692167', '101001624', '1010031975', '1010087179', '1010087623', '10101477', '1010470346', '1010673430', '101093029', '101093045', '1011572216', '1012150929', '1012212859', '1012328893', '101262930', '1013536888', '101362133', '101362650', '1014609273', '101471792', '1014785440', '1015118661', '1015584366', '101559400', '1015712668', '10160966', '101654506', '1016626169', '101669240', '1016887272', '1017675163', '1018057225', '1018148011', '101859883', '10188041', '1019077836', '101958970', '1019604187', '10

In [11]:
descriptions.values()

dict_values(['two young guys with shaggy hair look at their hands while hanging out in the yard', 'several men in hard hats are operating giant pulley system', 'child in pink dress is climbing up set of stairs in an entry way', 'someone in blue shirt and hat is standing on stair and leaning against window', 'two men one in gray shirt one in black shirt standing near stove', 'two people in the photo are playing the guitar and the other is poking at him', 'man sits in chair while holding large stuffed animal of lion', 'girl is on rollerskates talking on her cellphone standing in parking lot', 'an asian man wearing black suit stands near darkhaired woman and brownhaired woman', 'two men in germany jumping over rail at the same time without shirts', 'five ballet dancers caught mid jump in dancing studio with sunlight coming through window', 'three young men and young woman wearing sneakers are leaping in midair at the top of flight of concrete stairs', 'black dog and white dog with brown s

### Imagenes

#### Descarga de imagenes

In [12]:
!wget http://shannon.cs.illinois.edu/DenotationGraph/data/flickr30k-images.tar

--2019-08-29 01:01:01--  http://shannon.cs.illinois.edu/DenotationGraph/data/flickr30k-images.tar
Resolving shannon.cs.illinois.edu (shannon.cs.illinois.edu)... 18.220.149.166
Connecting to shannon.cs.illinois.edu (shannon.cs.illinois.edu)|18.220.149.166|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 4440780800 (4.1G) [application/x-tar]
Saving to: ‘flickr30k-images.tar.1’

flickr30k-images.ta 100%[===================>]   4.14G  66.0MB/s    in 58s     

2019-08-29 01:01:59 (72.4 MB/s) - ‘flickr30k-images.tar.1’ saved [4440780800/4440780800]



In [13]:
# Descomprimimos
!tar -vxf flickr30k-images.tar

flickr30k-images/
flickr30k-images/1000092795.jpg
flickr30k-images/10002456.jpg
flickr30k-images/1000268201.jpg
flickr30k-images/1000344755.jpg
flickr30k-images/1000366164.jpg
flickr30k-images/1000523639.jpg
flickr30k-images/1000919630.jpg
flickr30k-images/10010052.jpg
flickr30k-images/1001465944.jpg
flickr30k-images/1001545525.jpg
flickr30k-images/1001573224.jpg
flickr30k-images/1001633352.jpg
flickr30k-images/1001773457.jpg
flickr30k-images/1001896054.jpg
flickr30k-images/100197432.jpg
flickr30k-images/100207720.jpg
flickr30k-images/1002674143.jpg
flickr30k-images/1003163366.jpg
flickr30k-images/1003420127.jpg
flickr30k-images/1003428081.jpg
flickr30k-images/100444898.jpg
flickr30k-images/1005216151.jpg
flickr30k-images/100577935.jpg
flickr30k-images/1006452823.jpg
flickr30k-images/100652400.jpg
flickr30k-images/1007129816.jpg
flickr30k-images/100716317.jpg
flickr30k-images/1007205537.jpg
flickr30k-images/1007320043.jpg
flickr30k-images/100759042.jpg
flickr30k-images/10082347.jpg
fli

In [0]:
# elimino readme.txt para evitar problemas a la hora entrenar
# Si, la solución correcta sería comprobar que es una imagen antes de entrenar la red
# pero por el momento vale.

!rm flickr30k-images/readme.txt

#### Limpieza y preparacion de las imagenes

Las imagenes ya están todas preparadas para su procesado, sólo será necesario cambiar sus dimensiones a 224x224, pero este paso se realiza mientras extraemos las caracteristicas.

## Modelo





En este momento nos vamos a centrar en el extractor de caracteristicas.


#### Extracción de caracteristicas 


Podriamos crear un modelo de de redes neuronales para extraer las caracteristicas del conjunto de imagenes que hemos bajado, pero cuando hay gente muy lista que ha creado unos modelos ya probados, es mejor apoyarse en el trabajo de otros y extraer las características de las imagenes con un modelo (y unos pesos) ya entrenado.

Vamos a usar el VGG16. Este modelo es lento de aplicar, así que vamos a obtener las caracteristicas que nos da el modelo y las guardaremos en un archivo.

De esta manera, a la hora de entrenar el LSTM, el trabajo de la extracción de caracteristicas estará ya realizado, y no tendremos que sacar las mismas de cada imagen justo antes de entrar en la red neuronal recurrente.



In [15]:
!pip install tqdm

In [16]:
from os import listdir
from pickle import load, dump
from tqdm import tqdm
from numpy import array
from numpy import argmax
from pandas import DataFrame
from nltk.translate.bleu_score import corpus_bleu
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.utils import to_categorical
from keras.applications.vgg16 import VGG16
from keras.preprocessing.image import load_img, img_to_array
from keras.applications.vgg16 import preprocess_input
from keras.models import Model
from keras.layers import Input, Dense, Flatten, LSTM, RepeatVector, TimeDistributed, Embedding
from keras.layers.merge import concatenate
from keras.layers.pooling import GlobalMaxPooling2D

Using TensorFlow backend.


In [17]:
# extract features from each photo in the directory
def extract_features(directory):
  # load the model
  in_layer = Input(shape=(224, 224, 3))
  model = VGG16(include_top=False, input_tensor=in_layer)
  print(model.summary())
  # extract features from each photo
  features = dict()

  files_in_directory = listdir(directory)
  n_images = len(files_in_directory)
  for i, name in tqdm(enumerate(files_in_directory), total=n_images):
    # load an image from file
    filename = directory + '/' + name
    image = load_img(filename, target_size=(224, 224))
    # convert the image pixels to a numpy array
    image = img_to_array(image)
    # reshape data for the model
    image = image.reshape((1, image.shape[0], image.shape[1], image.shape[2]))
    # prepare the image for the VGG model
    image = preprocess_input(image)
    # get features
    feature = model.predict(image, verbose=0)
    # get image id
    image_id = name.split('.')[0]
    # store feature
    features[image_id] = feature
    # print('{} / {} > {}'.format(i, n_images, name))
  return features
# extract features from all images
directory = 'flickr30k-images'
features = extract_features(directory)
print('Extracted Features: %d' % len(features))
# save to file
dump(features, open('features.pkl', 'wb'))

W0829 01:02:45.460898 140502137550720 deprecation_wrapper.py:119] From /usr/local/lib/python3.6/dist-packages/keras/backend/tensorflow_backend.py:74: The name tf.get_default_graph is deprecated. Please use tf.compat.v1.get_default_graph instead.

W0829 01:02:45.519878 140502137550720 deprecation_wrapper.py:119] From /usr/local/lib/python3.6/dist-packages/keras/backend/tensorflow_backend.py:517: The name tf.placeholder is deprecated. Please use tf.compat.v1.placeholder instead.

W0829 01:02:45.540890 140502137550720 deprecation_wrapper.py:119] From /usr/local/lib/python3.6/dist-packages/keras/backend/tensorflow_backend.py:4138: The name tf.random_uniform is deprecated. Please use tf.random.uniform instead.

W0829 01:02:45.578577 140502137550720 deprecation_wrapper.py:119] From /usr/local/lib/python3.6/dist-packages/keras/backend/tensorflow_backend.py:3976: The name tf.nn.max_pool is deprecated. Please use tf.nn.max_pool2d instead.

W0829 01:02:45.979857 140502137550720 deprecation_wrapp

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         (None, 224, 224, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 224, 224, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 224, 224, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 112, 112, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 112, 112, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 112, 112, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 56, 56, 128)       0         
__________

100%|██████████| 31783/31783 [15:17<00:00, 34.63it/s]


Extracted Features: 31783


Tenemos 31783 descripciones y 31783 imagenes con sus caracteristicas extraidas. Tratar de entrenar un modelo con todos estos datos llevaría días, asi que por el momento vamos a seleccionar 1000 imagenes con las que trabajar, y con ellas generaremos nuestros conjuntos de entrenamiento, test y validación.


In [0]:
TRAINING_SET = 1000

import random
# fix random seed for reproducibility
random.seed(42)

def select_files_for_training(directory, n=TRAINING_SET):
  
  files_in_directory = listdir(directory)
  index_de_ficheros = random.sample(range(1, len(files_in_directory)), n)
  l = []
  for i in index_de_ficheros:
    imagen = files_in_directory[i]
    imagen = imagen[0:-4] #quitar la extension
    l.append(imagen)
  return l

def save_training_file_list(l, filename):
	lines = list()
	for desc in l:
		lines.append(desc)
	data = '\n'.join(lines)
	file = open(filename, 'w')
	file.write(data)
	file.close()
  
l = select_files_for_training('flickr30k-images')  
save_training_file_list(l, 'train-test-val-set.txt')

### Generar modelo LSTM base

A la hora de crear un modelo para luego mejorarlo podriamos intentar entrenar el modelo con todos los datos, pero es muy costoso computacioanlemte hablando, y a la hora de realizar mejoras, nos pasariamos días. 

Siguiendo las recomendaciones de [How to Use Small Experiments to Develop a Caption Generation Model in Keras](https://machinelearningmastery.com/develop-a-caption-generation-model-in-keras/) y tal y como he explicado previamente, voy a quedarme con solo unos pocos datos. Estudiar cómo se comporta el modelo con esos datos, es decir, ver que parametros podemos afinar en la red neuronal, y generalizar la respuesta para ellos.

Al realizar un entrenamiento tan escaso, los valores que vamos a tener de Accuracy van a a ser bajos, pero nos va a permitir realizar pequeños cambios en el mismo, y comprobar los efectos que tienen esos combios en nuestros resultados.

De nuevo, si tuviesemos recursos computacionales infinitos estos experimentos se realizarian con todo el dataset.


In [19]:
from pickle import load

# load doc into memory
def load_doc(filename):
	# open the file as read only
	file = open(filename, 'r')
	# read all text
	text = file.read()
	# close the file
	file.close()
	return text

# load a pre-defined list of photo identifiers
def load_set(filename):
	doc = load_doc(filename)
	dataset = list()
	# process line by line
	for line in doc.split('\n'):
		# skip empty lines
		if len(line) < 1:
			continue
		# get the image identifier
		identifier = line.split('.')[0]
		dataset.append(identifier)
	return set(dataset)

# split a dataset into train/test elements
def train_test_split(dataset,train,test,val):
  
  tr = int(len(dataset) * train / 100)
  te = int(len(dataset) * test / 100)
  va = int(len(dataset) * val / 100)
  
  # order keys so the split is consistent
  ordered = sorted(dataset)
	# return split dataset as two new sets
  return set(ordered[:tr]), set(ordered[tr:(tr+te)]), set(ordered[tr+te:tr+te+va])

# load clean descriptions into memory
def load_clean_descriptions(filename, dataset):
	# load document
	doc = load_doc(filename)
	descriptions = dict()
	for line in doc.split('\n'):
		# split line by white space
		tokens = line.split()
		# split id from description
		image_id, image_desc = tokens[0], tokens[1:]
		# skip images not in the set
		if image_id in dataset:
			# store
			descriptions[image_id] = 'startseq ' + ' '.join(image_desc) + ' endseq'
	return descriptions

# load photo features
def load_photo_features(filename, dataset):
	# load all features
	all_features = load(open(filename, 'rb'))
	# filter features
	features = {k: all_features[k] for k in dataset}
	return features

# load dev set
filename = 'train-test-val-set.txt'
dataset = load_set(filename)
print('Dataset: %d' % len(dataset))

# train-test split
train, test, val = train_test_split(dataset,10,10,5)
print (val)
print('Train=%d, Test=%d' % (len(train), len(test)))
# descriptions
train_descriptions = load_clean_descriptions('descriptions.txt', train)
test_descriptions = load_clean_descriptions('descriptions.txt', test)
val_descriptions = load_clean_descriptions('descriptions.txt', val)

print('Descriptions: train=%d, test=%d, val=%d' % (len(train_descriptions), 
                                                    len(test_descriptions), 
                                                    len(val_descriptions)))
# photo features
train_features = load_photo_features('features.pkl', train)
test_features = load_photo_features('features.pkl', test)
val_features = load_photo_features('features.pkl', val)

print('Photos: train=%d, test=%d, val=%d' % (len(train_features), 
                                             len(test_features),
                                             len(val_features)))

Dataset: 1000
{'2602279427', '2515247156', '2600386812', '265528702', '2600229816', '26653224', '2624947061', '2559260825', '2522995166', '2598775005', '2667242810', '2545363449', '2518853257', '2536957963', '2584487952', '2546149002', '2644920808', '2572988623', '2629027962', '2507349105', '2638207727', '2539933563', '2504991916', '2574194729', '2640260087', '2491343114', '2594336381', '2605591891', '2647862489', '2670637584', '2649216969', '267836606', '260231029', '2483993772', '2599908425', '2525898604', '254730529', '2592711202', '2506703854', '248174959', '264928854', '2508512414', '2657643451', '2502248149', '2537702182', '2648165716', '259520146', '247617035', '2538588862', '2642336024'}
Train=100, Test=100
Descriptions: train=100, test=100, val=50
Photos: train=100, test=100, val=50


Como estamos trabajando con tan pocas muestras, y para evitar encontrar resultados maravillosos por azar, entrenamos el modelo varias veces distintas. Esto aumenta el tiempo en el que extraemos conclusiones del modelo, pero sigue siendo mucho más corto que entrenar el modelo con todo el dataset.


Del dataset reducido que tenemos (100 imagenes)preparamos las secuencias de entrenamiento.

In [20]:
# Ahora codificamos nuestras descripciones a números
from keras.preprocessing.text import Tokenizer

# fit a tokenizer given caption descriptions
def create_tokenizer(descriptions):
	lines = list(descriptions.values())
	tokenizer = Tokenizer()
	tokenizer.fit_on_texts(lines)
	return tokenizer
 
# prepare tokenizer
tokenizer = create_tokenizer(descriptions)
vocab_size = len(tokenizer.word_index) + 1
print('Vocabulary Size: %d' % vocab_size)

Vocabulary Size: 13131


In [0]:
# create sequences of images, input sequences and output words for an image
def create_sequences(tokenizer, desc, image, max_length):
	Ximages, XSeq, y = list(), list(),list()
	vocab_size = len(tokenizer.word_index) + 1
	# integer encode the description
	seq = tokenizer.texts_to_sequences([desc])[0]
	# split one sequence into multiple X,y pairs
	for i in range(1, len(seq)):
		# select
		in_seq, out_seq = seq[:i], seq[i]
		# pad input sequence
		in_seq = pad_sequences([in_seq], maxlen=max_length)[0]
		# encode output sequence
		out_seq = to_categorical([out_seq], num_classes=vocab_size)[0]
		# store
		Ximages.append(image)
		XSeq.append(in_seq)
		y.append(out_seq)
	# Ximages, XSeq, y = array(Ximages), array(XSeq), array(y)
	return [Ximages, XSeq, y]

Este es el modelo básico con el que vamos a trabajar.

In [0]:
# define the captioning model
def define_model(vocab_size, max_length):
	# feature extractor (encoder)
	inputs1 = Input(shape=(7, 7, 512))
	fe1 = GlobalMaxPooling2D()(inputs1)
	fe2 = Dense(128, activation='relu')(fe1)
	fe3 = RepeatVector(max_length)(fe2)
	# embedding
	inputs2 = Input(shape=(max_length,))
	emb2 = Embedding(vocab_size, 50, mask_zero=True)(inputs2)
	emb3 = LSTM(256, return_sequences=True)(emb2)
	emb4 = TimeDistributed(Dense(128, activation='relu'))(emb3)
	# merge inputs
	merged = concatenate([fe3, emb4])
	# language model (decoder)
	lm2 = LSTM(500)(merged)
	lm3 = Dense(500, activation='relu')(lm2)
	outputs = Dense(vocab_size, activation='softmax')(lm3)
	# tie it together [image, seq] [word]
	model = Model(inputs=[inputs1, inputs2], outputs=outputs)
	model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
	print(model.summary())
	return model

In [0]:
# data generator, intended to be used in a call to model.fit_generator()
def data_generator(descriptions, features, tokenizer, max_length, n_step):
	# loop until we finish training
	while 1:
		# loop over photo identifiers in the dataset
		keys = list(descriptions.keys())
		for i in range(0, len(keys), n_step):
			Ximages, XSeq, y = list(), list(),list()
			for j in range(i, min(len(keys), i+n_step)):
				image_id = keys[j]
				# retrieve photo feature input
				image = features[image_id][0]
				# retrieve text input
				desc = descriptions[image_id]
				# generate input-output pairs
				in_img, in_seq, out_word = create_sequences(tokenizer, desc, image, max_length)
				for k in range(len(in_img)):
					Ximages.append(in_img[k])
					XSeq.append(in_seq[k])
					y.append(out_word[k])
			# yield this batch of samples to the model
			yield [[array(Ximages), array(XSeq)], array(y)]

Aqui se genera la secuencia que va a servir de entrenamiento a la LSTM

In [0]:
# map an integer to a word
def word_for_id(integer, tokenizer):
	for word, index in tokenizer.word_index.items():
		if index == integer:
			return word
	return None
 
# generate a description for an image
def generate_desc(model, tokenizer, photo, max_length):
	# seed the generation process
	in_text = 'startseq'
	# iterate over the whole length of the sequence
	for i in range(max_length):
		# integer encode input sequence
		sequence = tokenizer.texts_to_sequences([in_text])[0]
		# pad input
		sequence = pad_sequences([sequence], maxlen=max_length)
		# predict next word
		yhat = model.predict([photo,sequence], verbose=0)
		# convert probability to integer
		yhat = argmax(yhat)
		# map integer to word
		word = word_for_id(yhat, tokenizer)
		# stop if we cannot map the word
		if word is None:
			break
		# append as input for generating the next word
		in_text += ' ' + word
		# stop if we predict the end of the sequence
		if word == 'endseq':
			break
	return in_text
 


Y con la funcion [Bleu](https://es.wikipedia.org/wiki/BLEU) evaluamos la calidad de la secuencia generada por nuestra red.

In [0]:
# evaluate the skill of the model
def evaluate_model(model, descriptions, photos, tokenizer, max_length):
	actual, predicted = list(), list()
	# step over the whole set
	for key, desc in descriptions.items():
		# generate description
		yhat = generate_desc(model, tokenizer, photos[key], max_length)
		# store actual and predicted
		actual.append([desc.split()])
		predicted.append(yhat.split())
	# calculate BLEU score
	bleu = corpus_bleu(actual, predicted)
	return bleu

Ejecutamos el primer modelo 3 veces y almacenamos los distintos resultados para su posterior analisis.

In [26]:
# prepare tokenizer
tokenizer = create_tokenizer(train_descriptions)
vocab_size = len(tokenizer.word_index) + 1
print('Vocabulary Size: %d' % vocab_size)
# determine the maximum sequence length
max_length = max(len(s.split()) for s in list(train_descriptions.values()))
print('Description Length: %d' % max_length)
 
# define experiment
model_name = 'baseline1'
verbose = 1
n_epochs = 25
n_photos_per_update = 2
n_batches_per_epoch = int(len(train) / n_photos_per_update)
n_repeats = 3
 
# run experiment
train_results, test_results = list(), list()
for i in range(n_repeats):
	# define the model
	model = define_model(vocab_size, max_length)
	# fit model
	model.fit_generator(data_generator(train_descriptions, train_features, tokenizer, max_length, n_photos_per_update), steps_per_epoch=n_batches_per_epoch, epochs=n_epochs, verbose=verbose)
	# evaluate model on training data
	train_score = evaluate_model(model, train_descriptions, train_features, tokenizer, max_length)
	test_score = evaluate_model(model, test_descriptions, test_features, tokenizer, max_length)
	# store
	train_results.append(train_score)
	test_results.append(test_score)
	print('>%d: train=%f test=%f' % ((i+1), train_score, test_score))
# save results to file
df = DataFrame()
df['train'] = train_results
df['test'] = test_results
print(df.describe())
df.to_csv(model_name+'.csv', index=False)

Vocabulary Size: 591
Description Length: 35


W0829 01:18:36.919805 140502137550720 deprecation.py:323] From /usr/local/lib/python3.6/dist-packages/keras/backend/tensorflow_backend.py:2974: add_dispatch_support.<locals>.wrapper (from tensorflow.python.ops.array_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where
W0829 01:18:37.667130 140502137550720 deprecation_wrapper.py:119] From /usr/local/lib/python3.6/dist-packages/keras/optimizers.py:790: The name tf.train.Optimizer is deprecated. Please use tf.compat.v1.train.Optimizer instead.



__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_2 (InputLayer)            (None, 7, 7, 512)    0                                            
__________________________________________________________________________________________________
input_3 (InputLayer)            (None, 35)           0                                            
__________________________________________________________________________________________________
global_max_pooling2d_1 (GlobalM (None, 512)          0           input_2[0][0]                    
__________________________________________________________________________________________________
embedding_1 (Embedding)         (None, 35, 50)       29550       input_3[0][0]                    
__________________________________________________________________________________________________
dense_1 (D

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 2-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>1: train=0.000346 test=0.000570
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_4 (InputLayer)            (None, 7, 7, 512)    0                                            
__________________________________________________________________________________________________
input_5 (InputLayer)            (None, 35)           0                                            
__________________________________________________________________________________________________
global_max_pooling2d_2 (GlobalM (None, 512)          0           input_4[0][0]                    
__________________________________________________________________________________________________
embedding_2 (Embedding)         (None, 35, 50)       29550       input_5[0][0]                    
____________________________________________________________________________

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 2-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>2: train=0.000346 test=0.000570
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_6 (InputLayer)            (None, 7, 7, 512)    0                                            
__________________________________________________________________________________________________
input_7 (InputLayer)            (None, 35)           0                                            
__________________________________________________________________________________________________
global_max_pooling2d_3 (GlobalM (None, 512)          0           input_6[0][0]                    
__________________________________________________________________________________________________
embedding_3 (Embedding)         (None, 35, 50)       29550       input_7[0][0]                    
____________________________________________________________________________

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 2-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>3: train=0.000346 test=0.000570
          train     test
count  3.000000  3.00000
mean   0.000346  0.00057
std    0.000000  0.00000
min    0.000346  0.00057
25%    0.000346  0.00057
50%    0.000346  0.00057
75%    0.000346  0.00057
max    0.000346  0.00057


Tenemos nuestro primer experimento, que nos servirá para establecer un benchmark para comparar como se comporta el modelo con distintos cambios en alguna de sus capas.


## Mejoras

Ahora vamos a ir cambiando el modelo para ver si obtenemos mejores resultados.

### Entrada del LSTM

En nuestro modelo inicial, las caracteristicas de la foto (128) y la secuencia de texto (128) se concatenan y se meten en la red LSTM. Probamos a ver como afecta el cambiar el tamaño de la las caracteristicas y la descripcion.

#### Vector de entrada de la LSTM a 128 (size_sm_fixed_vec)

Cambiamos de 128 cáracteristicas y 128 elementos en la descripción a 64 (que al concatenarse hacen un vector de entrada de 128).

In [27]:
# define the captioning model
def define_model(vocab_size, max_length):
	# feature extractor (encoder)
	inputs1 = Input(shape=(7, 7, 512))
	fe1 = GlobalMaxPooling2D()(inputs1)
	fe2 = Dense(64, activation='relu')(fe1)
	fe3 = RepeatVector(max_length)(fe2)
	# embedding
	inputs2 = Input(shape=(max_length,))
	emb2 = Embedding(vocab_size, 50, mask_zero=True)(inputs2)
	emb3 = LSTM(256, return_sequences=True)(emb2)
	emb4 = TimeDistributed(Dense(64, activation='relu'))(emb3) #cambio en esta (de 128 a 64)
	# merge inputs
	merged = concatenate([fe3, emb4])
	# language model (decoder)
	lm2 = LSTM(500)(merged)
	lm3 = Dense(500, activation='relu')(lm2)
	outputs = Dense(vocab_size, activation='softmax')(lm3)
	# tie it together [image, seq] [word]
	model = Model(inputs=[inputs1, inputs2], outputs=outputs)
	model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
	return model

	


# prepare tokenizer
tokenizer = create_tokenizer(train_descriptions)
vocab_size = len(tokenizer.word_index) + 1
print('Vocabulary Size: %d' % vocab_size)
# determine the maximum sequence length
max_length = max(len(s.split()) for s in list(train_descriptions.values()))
print('Description Length: %d' % max_length)
 
# define experiment
model_name = 'size_sm_fixed_vec'
verbose = 1
n_epochs = 25
n_photos_per_update = 2
n_batches_per_epoch = int(len(train) / n_photos_per_update)
n_repeats = 3
 
# run experiment
train_results, test_results = list(), list()
for i in range(n_repeats):
	# define the model
	model = define_model(vocab_size, max_length)
	# fit model
	model.fit_generator(data_generator(train_descriptions, train_features, tokenizer, max_length, n_photos_per_update), steps_per_epoch=n_batches_per_epoch, epochs=n_epochs, verbose=verbose)
	# evaluate model on training data
	train_score = evaluate_model(model, train_descriptions, train_features, tokenizer, max_length)
	test_score = evaluate_model(model, test_descriptions, test_features, tokenizer, max_length)
	# store
	train_results.append(train_score)
	test_results.append(test_score)
	print('>%d: train=%f test=%f' % ((i+1), train_score, test_score))
# save results to file
df = DataFrame()
df['train'] = train_results
df['test'] = test_results
print(df.describe())
df.to_csv(model_name+'.csv', index=False)

Vocabulary Size: 591
Description Length: 35
Epoch 1/25
50/50 [==============================] - 13s 262ms/step - loss: 5.8779 - acc: 0.0491
Epoch 2/25
50/50 [==============================] - 10s 200ms/step - loss: 5.5679 - acc: 0.0591
Epoch 3/25
50/50 [==============================] - 10s 200ms/step - loss: 5.5553 - acc: 0.0617
Epoch 4/25
50/50 [==============================] - 10s 201ms/step - loss: 5.5547 - acc: 0.0577
Epoch 5/25
50/50 [==============================] - 10s 200ms/step - loss: 5.5386 - acc: 0.0617
Epoch 6/25
50/50 [==============================] - 10s 200ms/step - loss: 5.5101 - acc: 0.0594
Epoch 7/25
50/50 [==============================] - 10s 200ms/step - loss: 5.5021 - acc: 0.0586
Epoch 8/25
50/50 [==============================] - 10s 199ms/step - loss: 5.4810 - acc: 0.0609
Epoch 9/25
50/50 [==============================] - 10s 197ms/step - loss: 5.4804 - acc: 0.0609
Epoch 10/25
50/50 [==============================] - 10s 200ms/step - loss: 5.5011 - acc: 0.

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 3-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>1: train=0.115510 test=0.073329
Epoch 1/25
50/50 [==============================] - 13s 267ms/step - loss: 5.8788 - acc: 0.0514
Epoch 2/25
50/50 [==============================] - 10s 196ms/step - loss: 5.5427 - acc: 0.0609
Epoch 3/25
50/50 [==============================] - 10s 198ms/step - loss: 5.5147 - acc: 0.0581
Epoch 4/25
50/50 [==============================] - 10s 196ms/step - loss: 5.5148 - acc: 0.0591
Epoch 5/25
50/50 [==============================] - 10s 195ms/step - loss: 5.5182 - acc: 0.0602
Epoch 6/25
50/50 [==============================] - 10s 194ms/step - loss: 5.5071 - acc: 0.0576
Epoch 7/25
50/50 [==============================] - 10s 197ms/step - loss: 5.4351 - acc: 0.0564
Epoch 8/25
50/50 [==============================] - 10s 197ms/step - loss: 5.4235 - acc: 0.0626
Epoch 9/25
50/50 [==============================] - 10s 198ms/step - loss: 5.3950 - acc: 0.0597
Epoch 10/25
50/50 [==============================] - 10s 198ms/step - loss: 5.4001 - acc: 0.0605
Epoch 

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 3-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>2: train=0.066704 test=0.075890
Epoch 1/25
50/50 [==============================] - 14s 278ms/step - loss: 5.8677 - acc: 0.0495
Epoch 2/25
50/50 [==============================] - 10s 200ms/step - loss: 5.5602 - acc: 0.0604
Epoch 3/25
50/50 [==============================] - 10s 200ms/step - loss: 5.5232 - acc: 0.0610
Epoch 4/25
50/50 [==============================] - 10s 200ms/step - loss: 5.5307 - acc: 0.0562
Epoch 5/25
50/50 [==============================] - 10s 198ms/step - loss: 5.5665 - acc: 0.0598
Epoch 6/25
50/50 [==============================] - 10s 200ms/step - loss: 5.5566 - acc: 0.0569
Epoch 7/25
50/50 [==============================] - 10s 202ms/step - loss: 5.5484 - acc: 0.0596
Epoch 8/25
50/50 [==============================] - 10s 200ms/step - loss: 5.5151 - acc: 0.0617
Epoch 9/25
50/50 [==============================] - 10s 199ms/step - loss: 5.4738 - acc: 0.0592
Epoch 10/25
50/50 [==============================] - 10s 198ms/step - loss: 5.4788 - acc: 0.0603
Epoch 

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 4-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>3: train=0.028092 test=0.024320
          train      test
count  3.000000  3.000000
mean   0.070102  0.057846
std    0.043808  0.029063
min    0.028092  0.024320
25%    0.047398  0.048825
50%    0.066704  0.073329
75%    0.091107  0.074610
max    0.115510  0.075890


#### Vector de entrada de la LSTM a 512 (size_lg_fixed_vec)

Y ahora duplicamos a 256.

In [28]:
# define the captioning model
def define_model(vocab_size, max_length):
	# feature extractor (encoder)
	inputs1 = Input(shape=(7, 7, 512))
	fe1 = GlobalMaxPooling2D()(inputs1)
	fe2 = Dense(256, activation='relu')(fe1)
	fe3 = RepeatVector(max_length)(fe2)
	# embedding
	inputs2 = Input(shape=(max_length,))
	emb2 = Embedding(vocab_size, 50, mask_zero=True)(inputs2)
	emb3 = LSTM(256, return_sequences=True)(emb2)
	emb4 = TimeDistributed(Dense(256, activation='relu'))(emb3)
	# merge inputs
	merged = concatenate([fe3, emb4])
	# language model (decoder)
	lm2 = LSTM(500)(merged)
	lm3 = Dense(500, activation='relu')(lm2)
	outputs = Dense(vocab_size, activation='softmax')(lm3)
	# tie it together [image, seq] [word]
	model = Model(inputs=[inputs1, inputs2], outputs=outputs)
	model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
	return model

# prepare tokenizer
tokenizer = create_tokenizer(train_descriptions)
vocab_size = len(tokenizer.word_index) + 1
print('Vocabulary Size: %d' % vocab_size)
# determine the maximum sequence length
max_length = max(len(s.split()) for s in list(train_descriptions.values()))
print('Description Length: %d' % max_length)
 
# define experiment
model_name = 'size_lg_fixed_vec'
verbose = 1
n_epochs = 25
n_photos_per_update = 2
n_batches_per_epoch = int(len(train) / n_photos_per_update)
n_repeats = 3
 
# run experiment
train_results, test_results = list(), list()
for i in range(n_repeats):
	# define the model
	model = define_model(vocab_size, max_length)
	# fit model
	model.fit_generator(data_generator(train_descriptions, train_features, tokenizer, max_length, n_photos_per_update), steps_per_epoch=n_batches_per_epoch, epochs=n_epochs, verbose=verbose)
	# evaluate model on training data
	train_score = evaluate_model(model, train_descriptions, train_features, tokenizer, max_length)
	test_score = evaluate_model(model, test_descriptions, test_features, tokenizer, max_length)
	# store
	train_results.append(train_score)
	test_results.append(test_score)
	print('>%d: train=%f test=%f' % ((i+1), train_score, test_score))
# save results to file
df = DataFrame()
df['train'] = train_results
df['test'] = test_results
print(df.describe())
df.to_csv(model_name+'.csv', index=False)

Vocabulary Size: 591
Description Length: 35
Epoch 1/25
50/50 [==============================] - 14s 285ms/step - loss: 5.8853 - acc: 0.0479
Epoch 2/25
50/50 [==============================] - 10s 197ms/step - loss: 5.6185 - acc: 0.0605
Epoch 3/25
50/50 [==============================] - 10s 197ms/step - loss: 5.5578 - acc: 0.0567
Epoch 4/25
50/50 [==============================] - 10s 196ms/step - loss: 5.5209 - acc: 0.0586
Epoch 5/25
50/50 [==============================] - 10s 195ms/step - loss: 5.5246 - acc: 0.0549
Epoch 6/25
50/50 [==============================] - 10s 195ms/step - loss: 5.5017 - acc: 0.0585
Epoch 7/25
50/50 [==============================] - 10s 196ms/step - loss: 5.4890 - acc: 0.0609
Epoch 8/25
50/50 [==============================] - 10s 196ms/step - loss: 5.4959 - acc: 0.0608
Epoch 9/25
50/50 [==============================] - 10s 195ms/step - loss: 5.4820 - acc: 0.0617
Epoch 10/25
50/50 [==============================] - 10s 196ms/step - loss: 5.4772 - acc: 0.

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 3-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>1: train=0.003413 test=0.004455
Epoch 1/25
50/50 [==============================] - 14s 289ms/step - loss: 5.8861 - acc: 0.0520
Epoch 2/25
50/50 [==============================] - 10s 196ms/step - loss: 5.5946 - acc: 0.0565
Epoch 3/25
50/50 [==============================] - 10s 197ms/step - loss: 5.5640 - acc: 0.0567
Epoch 4/25
50/50 [==============================] - 10s 196ms/step - loss: 5.5307 - acc: 0.0578
Epoch 5/25
50/50 [==============================] - 10s 195ms/step - loss: 5.5035 - acc: 0.0617
Epoch 6/25
50/50 [==============================] - 10s 196ms/step - loss: 5.4925 - acc: 0.0597
Epoch 7/25
50/50 [==============================] - 10s 195ms/step - loss: 5.4853 - acc: 0.0594
Epoch 8/25
50/50 [==============================] - 10s 196ms/step - loss: 5.4821 - acc: 0.0617
Epoch 9/25
50/50 [==============================] - 10s 196ms/step - loss: 5.4766 - acc: 0.0613
Epoch 10/25
50/50 [==============================] - 10s 197ms/step - loss: 5.4758 - acc: 0.0617
Epoch 

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 3-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>2: train=0.003413 test=0.004309
Epoch 1/25
50/50 [==============================] - 15s 301ms/step - loss: 5.8813 - acc: 0.0528
Epoch 2/25
50/50 [==============================] - 10s 196ms/step - loss: 5.5954 - acc: 0.0588
Epoch 3/25
50/50 [==============================] - 10s 198ms/step - loss: 5.5655 - acc: 0.0591
Epoch 4/25
50/50 [==============================] - 10s 197ms/step - loss: 5.5286 - acc: 0.0617
Epoch 5/25
50/50 [==============================] - 10s 196ms/step - loss: 5.5066 - acc: 0.0612
Epoch 6/25
50/50 [==============================] - 10s 195ms/step - loss: 5.4996 - acc: 0.0590
Epoch 7/25
50/50 [==============================] - 10s 196ms/step - loss: 5.4898 - acc: 0.0593
Epoch 8/25
50/50 [==============================] - 10s 195ms/step - loss: 5.4859 - acc: 0.0590
Epoch 9/25
50/50 [==============================] - 10s 197ms/step - loss: 5.4823 - acc: 0.0605
Epoch 10/25
50/50 [==============================] - 10s 197ms/step - loss: 5.4792 - acc: 0.0617
Epoch 

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 2-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>3: train=0.000346 test=0.000570
          train      test
count  3.000000  3.000000
mean   0.002391  0.003111
std    0.001771  0.002202
min    0.000346  0.000570
25%    0.001880  0.002439
50%    0.003413  0.004309
75%    0.003413  0.004382
max    0.003413  0.004455


### Secuenciador

El secuenciador es la parte del modelo que genera las secuencias y que se entrena tambien con una LSTM. Podemos aumentar y disminur su 'memoria'

#### Modelo con poca memoria en el secuenciador(size_sm_seq_model)

In [29]:
# define the captioning model
def define_model(vocab_size, max_length):
	# feature extractor (encoder)
	inputs1 = Input(shape=(7, 7, 512))
	fe1 = GlobalMaxPooling2D()(inputs1)
	fe2 = Dense(128, activation='relu')(fe1)
	fe3 = RepeatVector(max_length)(fe2)
	# embedding
	inputs2 = Input(shape=(max_length,))
	emb2 = Embedding(vocab_size, 50, mask_zero=True)(inputs2)
	emb3 = LSTM(128, return_sequences=True)(emb2)
	emb4 = TimeDistributed(Dense(128, activation='relu'))(emb3)
	# merge inputs
	merged = concatenate([fe3, emb4])
	# language model (decoder)
	lm2 = LSTM(500)(merged)
	lm3 = Dense(500, activation='relu')(lm2)
	outputs = Dense(vocab_size, activation='softmax')(lm3)
	# tie it together [image, seq] [word]
	model = Model(inputs=[inputs1, inputs2], outputs=outputs)
	model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
	return model


# prepare tokenizer
tokenizer = create_tokenizer(train_descriptions)
vocab_size = len(tokenizer.word_index) + 1
print('Vocabulary Size: %d' % vocab_size)
# determine the maximum sequence length
max_length = max(len(s.split()) for s in list(train_descriptions.values()))
print('Description Length: %d' % max_length)
 
# define experiment
model_name = 'size_sm_seq_model'
verbose = 1
n_epochs = 25
n_photos_per_update = 2
n_batches_per_epoch = int(len(train) / n_photos_per_update)
n_repeats = 3
 
# run experiment
train_results, test_results = list(), list()
for i in range(n_repeats):
	# define the model
	model = define_model(vocab_size, max_length)
	# fit model
	model.fit_generator(data_generator(train_descriptions, train_features, tokenizer, max_length, n_photos_per_update), steps_per_epoch=n_batches_per_epoch, epochs=n_epochs, verbose=verbose)
	# evaluate model on training data
	train_score = evaluate_model(model, train_descriptions, train_features, tokenizer, max_length)
	test_score = evaluate_model(model, test_descriptions, test_features, tokenizer, max_length)
	# store
	train_results.append(train_score)
	test_results.append(test_score)
	print('>%d: train=%f test=%f' % ((i+1), train_score, test_score))
# save results to file
df = DataFrame()
df['train'] = train_results
df['test'] = test_results
print(df.describe())
df.to_csv(model_name+'.csv', index=False)

Vocabulary Size: 591
Description Length: 35
Epoch 1/25
50/50 [==============================] - 15s 303ms/step - loss: 5.8596 - acc: 0.0524
Epoch 2/25
50/50 [==============================] - 10s 193ms/step - loss: 5.5757 - acc: 0.0592
Epoch 3/25
50/50 [==============================] - 10s 197ms/step - loss: 5.5602 - acc: 0.0573
Epoch 4/25
50/50 [==============================] - 10s 193ms/step - loss: 5.5767 - acc: 0.0586
Epoch 5/25
50/50 [==============================] - 9s 190ms/step - loss: 5.5355 - acc: 0.0583
Epoch 6/25
50/50 [==============================] - 9s 189ms/step - loss: 5.5034 - acc: 0.0588
Epoch 7/25
50/50 [==============================] - 9s 188ms/step - loss: 5.4980 - acc: 0.0587
Epoch 8/25
50/50 [==============================] - 9s 188ms/step - loss: 5.4910 - acc: 0.0597
Epoch 9/25
50/50 [==============================] - 9s 188ms/step - loss: 5.4891 - acc: 0.0600
Epoch 10/25
50/50 [==============================] - 9s 190ms/step - loss: 5.4811 - acc: 0.0617
E

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 2-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>1: train=0.000346 test=0.000570
Epoch 1/25
50/50 [==============================] - 16s 313ms/step - loss: 5.8669 - acc: 0.0540
Epoch 2/25
50/50 [==============================] - 10s 194ms/step - loss: 5.5803 - acc: 0.0557
Epoch 3/25
50/50 [==============================] - 10s 194ms/step - loss: 5.5650 - acc: 0.0558
Epoch 4/25
50/50 [==============================] - 10s 194ms/step - loss: 5.5260 - acc: 0.0564
Epoch 5/25
50/50 [==============================] - 10s 193ms/step - loss: 5.5057 - acc: 0.0573
Epoch 6/25
50/50 [==============================] - 10s 193ms/step - loss: 5.5007 - acc: 0.0578
Epoch 7/25
50/50 [==============================] - 10s 192ms/step - loss: 5.4929 - acc: 0.0617
Epoch 8/25
50/50 [==============================] - 10s 196ms/step - loss: 5.5006 - acc: 0.0590
Epoch 9/25
50/50 [==============================] - 10s 196ms/step - loss: 5.4842 - acc: 0.0617
Epoch 10/25
50/50 [==============================] - 10s 192ms/step - loss: 5.4791 - acc: 0.0617
Epoch 

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 2-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>2: train=0.000346 test=0.000570
Epoch 1/25
50/50 [==============================] - 16s 323ms/step - loss: 5.8700 - acc: 0.0486
Epoch 2/25
50/50 [==============================] - 10s 194ms/step - loss: 5.5963 - acc: 0.0609
Epoch 3/25
50/50 [==============================] - 10s 194ms/step - loss: 5.5566 - acc: 0.0596
Epoch 4/25
50/50 [==============================] - 10s 194ms/step - loss: 5.5281 - acc: 0.0613
Epoch 5/25
50/50 [==============================] - 10s 195ms/step - loss: 5.5172 - acc: 0.0573
Epoch 6/25
50/50 [==============================] - 10s 193ms/step - loss: 5.5094 - acc: 0.0583
Epoch 7/25
50/50 [==============================] - 10s 195ms/step - loss: 5.4972 - acc: 0.0616
Epoch 8/25
50/50 [==============================] - 10s 195ms/step - loss: 5.4966 - acc: 0.0572
Epoch 9/25
50/50 [==============================] - 10s 193ms/step - loss: 5.5043 - acc: 0.0583
Epoch 10/25
50/50 [==============================] - 10s 192ms/step - loss: 5.4909 - acc: 0.0617
Epoch 

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 3-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>3: train=0.003289 test=0.004309
          train      test
count  3.000000  3.000000
mean   0.001327  0.001816
std    0.001699  0.002159
min    0.000346  0.000570
25%    0.000346  0.000570
50%    0.000346  0.000570
75%    0.001817  0.002439
max    0.003289  0.004309


#### Modelo con mucha memoria en el secuenciador (size_lg_seq_model)

Añadimos una nueva capa de 256 neuronas despues de la primera

In [43]:
# define the captioning model
def define_model(vocab_size, max_length):
	# feature extractor (encoder)
    inputs1 = Input(shape=(7, 7, 512))
    fe1 = GlobalMaxPooling2D()(inputs1)
    fe2 = Dense(128, activation='relu')(fe1)
    fe3 = RepeatVector(max_length)(fe2)
	# embedding
    inputs2 = Input(shape=(max_length,))
    emb2 = Embedding(vocab_size, 50, mask_zero=True)(inputs2)
    emb3 = LSTM(256, return_sequences=True)(emb2) 
    # se añade esta nueva capa 
    emb4 = LSTM(256, return_sequences=True)(emb3)
    emb5 = TimeDistributed(Dense(128, activation='relu'))(emb4)
	
    # merge inputs
    merged = concatenate([fe3, emb5])
	# language model (decoder)
    lm2 = LSTM(500)(merged)
    lm3 = Dense(500, activation='relu')(lm2)
    outputs = Dense(vocab_size, activation='softmax')(lm3)
	# tie it together [image, seq] [word]
    model = Model(inputs=[inputs1, inputs2], outputs=outputs)
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
    
    return model



# prepare tokenizer
tokenizer = create_tokenizer(train_descriptions)
vocab_size = len(tokenizer.word_index) + 1
print('Vocabulary Size: %d' % vocab_size)
# determine the maximum sequence length
max_length = max(len(s.split()) for s in list(train_descriptions.values()))
print('Description Length: %d' % max_length)
 
# define experiment
model_name = 'size_lg_seq_model'
verbose = 1
n_epochs = 25
n_photos_per_update = 2
n_batches_per_epoch = int(len(train) / n_photos_per_update)
n_repeats = 3
 
# run experiment
train_results, test_results = list(), list()
for i in range(n_repeats):
	# define the model
	model = define_model(vocab_size, max_length)
	# fit model
	model.fit_generator(data_generator(train_descriptions, train_features, tokenizer, max_length, n_photos_per_update), steps_per_epoch=n_batches_per_epoch, epochs=n_epochs, verbose=verbose)
	# evaluate model on training data
	train_score = evaluate_model(model, train_descriptions, train_features, tokenizer, max_length)
	test_score = evaluate_model(model, test_descriptions, test_features, tokenizer, max_length)
	# store
	train_results.append(train_score)
	test_results.append(test_score)
	print('>%d: train=%f test=%f' % ((i+1), train_score, test_score))
# save results to file
df = DataFrame()
df['train'] = train_results
df['test'] = test_results
print(df.describe())
df.to_csv(model_name+'.csv', index=False)

Vocabulary Size: 591
Description Length: 35
Epoch 1/25
50/50 [==============================] - 20s 404ms/step - loss: 5.8797 - acc: 0.0503
Epoch 2/25
50/50 [==============================] - 13s 259ms/step - loss: 5.5941 - acc: 0.0580
Epoch 3/25
50/50 [==============================] - 13s 262ms/step - loss: 5.5786 - acc: 0.0557
Epoch 4/25
50/50 [==============================] - 13s 262ms/step - loss: 5.5395 - acc: 0.0584
Epoch 5/25
50/50 [==============================] - 13s 263ms/step - loss: 5.5145 - acc: 0.0591
Epoch 6/25
50/50 [==============================] - 13s 263ms/step - loss: 5.5128 - acc: 0.0579
Epoch 7/25
50/50 [==============================] - 13s 261ms/step - loss: 5.4964 - acc: 0.0617
Epoch 8/25
50/50 [==============================] - 13s 259ms/step - loss: 5.5156 - acc: 0.0578
Epoch 9/25
50/50 [==============================] - 13s 258ms/step - loss: 5.5033 - acc: 0.0598
Epoch 10/25
50/50 [==============================] - 13s 259ms/step - loss: 5.4861 - acc: 0.

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 2-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>1: train=0.000346 test=0.000570
Epoch 1/25
50/50 [==============================] - 21s 424ms/step - loss: 5.8735 - acc: 0.0527
Epoch 2/25
50/50 [==============================] - 13s 257ms/step - loss: 5.5840 - acc: 0.0586
Epoch 3/25
50/50 [==============================] - 13s 258ms/step - loss: 5.5905 - acc: 0.0566
Epoch 4/25
50/50 [==============================] - 13s 259ms/step - loss: 5.5446 - acc: 0.0602
Epoch 5/25
50/50 [==============================] - 13s 259ms/step - loss: 5.5248 - acc: 0.0587
Epoch 6/25
50/50 [==============================] - 13s 261ms/step - loss: 5.5128 - acc: 0.0617
Epoch 7/25
50/50 [==============================] - 13s 260ms/step - loss: 5.4981 - acc: 0.0617
Epoch 8/25
50/50 [==============================] - 13s 258ms/step - loss: 5.4938 - acc: 0.0590
Epoch 9/25
50/50 [==============================] - 13s 260ms/step - loss: 5.4939 - acc: 0.0600
Epoch 10/25
50/50 [==============================] - 13s 260ms/step - loss: 5.4805 - acc: 0.0579
Epoch 

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 2-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>2: train=0.000361 test=0.000619
Epoch 1/25
50/50 [==============================] - 22s 431ms/step - loss: 5.8840 - acc: 0.0492
Epoch 2/25
50/50 [==============================] - 13s 262ms/step - loss: 5.6027 - acc: 0.0539
Epoch 3/25
50/50 [==============================] - 13s 260ms/step - loss: 5.5692 - acc: 0.0602
Epoch 4/25
50/50 [==============================] - 13s 261ms/step - loss: 5.5286 - acc: 0.0583
Epoch 5/25
50/50 [==============================] - 13s 257ms/step - loss: 5.5176 - acc: 0.0617
Epoch 6/25
50/50 [==============================] - 13s 258ms/step - loss: 5.4982 - acc: 0.0595
Epoch 7/25
50/50 [==============================] - 13s 258ms/step - loss: 5.4918 - acc: 0.0617
Epoch 8/25
50/50 [==============================] - 13s 260ms/step - loss: 5.4853 - acc: 0.0617
Epoch 9/25
50/50 [==============================] - 13s 264ms/step - loss: 5.4851 - acc: 0.0600
Epoch 10/25
50/50 [==============================] - 13s 264ms/step - loss: 5.4815 - acc: 0.0617
Epoch 

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 2-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>3: train=0.005917 test=0.009047
          train      test
count  3.000000  3.000000
mean   0.002208  0.003412
std    0.003212  0.004880
min    0.000346  0.000570
25%    0.000354  0.000594
50%    0.000361  0.000619
75%    0.003139  0.004833
max    0.005917  0.009047


#### Cambio en la dimensionalidad de la capa embedding del secuenciador (size_em_seq_model)

Intentamos incrementar la capacidad de vocabulario aumentando de 50 a 100 dimensiones

In [46]:
# define the captioning model
def define_model(vocab_size, max_length):
	# feature extractor (encoder)
    inputs1 = Input(shape=(7, 7, 512))
    fe1 = GlobalMaxPooling2D()(inputs1)
    fe2 = Dense(128, activation='relu')(fe1)
    fe3 = RepeatVector(max_length)(fe2)
	# embedding
    inputs2 = Input(shape=(max_length,))
	
    #cambia esta
    emb2 = Embedding(vocab_size, 100, mask_zero=True)(inputs2)
	
    emb3 = LSTM(256, return_sequences=True)(emb2)
    emb4 = TimeDistributed(Dense(128, activation='relu'))(emb3)
	# merge inputs
    merged = concatenate([fe3, emb4])
	# language model (decoder)
    lm2 = LSTM(500)(merged)
    lm3 = Dense(500, activation='relu')(lm2)
    outputs = Dense(vocab_size, activation='softmax')(lm3)
	# tie it together [image, seq] [word]
    model = Model(inputs=[inputs1, inputs2], outputs=outputs)
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
	
    return model



# prepare tokenizer
tokenizer = create_tokenizer(train_descriptions)
vocab_size = len(tokenizer.word_index) + 1
print('Vocabulary Size: %d' % vocab_size)
# determine the maximum sequence length
max_length = max(len(s.split()) for s in list(train_descriptions.values()))
print('Description Length: %d' % max_length)
 
# define experiment
model_name = 'size_em_seq_model'
verbose = 1
n_epochs = 25
n_photos_per_update = 2
n_batches_per_epoch = int(len(train) / n_photos_per_update)
n_repeats = 3
 
# run experiment
train_results, test_results = list(), list()
for i in range(n_repeats):
	# define the model
	model = define_model(vocab_size, max_length)
	# fit model
	model.fit_generator(data_generator(train_descriptions, train_features, tokenizer, max_length, n_photos_per_update), steps_per_epoch=n_batches_per_epoch, epochs=n_epochs, verbose=verbose)
	# evaluate model on training data
	train_score = evaluate_model(model, train_descriptions, train_features, tokenizer, max_length)
	test_score = evaluate_model(model, test_descriptions, test_features, tokenizer, max_length)
	# store
	train_results.append(train_score)
	test_results.append(test_score)
	print('>%d: train=%f test=%f' % ((i+1), train_score, test_score))
# save results to file
df = DataFrame()
df['train'] = train_results
df['test'] = test_results
print(df.describe())
df.to_csv(model_name+'.csv', index=False)

Vocabulary Size: 591
Description Length: 35
Epoch 1/25
50/50 [==============================] - 18s 358ms/step - loss: 5.8802 - acc: 0.0544
Epoch 2/25
50/50 [==============================] - 10s 195ms/step - loss: 5.5954 - acc: 0.0609
Epoch 3/25
50/50 [==============================] - 10s 197ms/step - loss: 5.5624 - acc: 0.0600
Epoch 4/25
50/50 [==============================] - 10s 196ms/step - loss: 5.5388 - acc: 0.0605
Epoch 5/25
50/50 [==============================] - 10s 194ms/step - loss: 5.5316 - acc: 0.0592
Epoch 6/25
50/50 [==============================] - 10s 193ms/step - loss: 5.5089 - acc: 0.0565
Epoch 7/25
50/50 [==============================] - 10s 193ms/step - loss: 5.5000 - acc: 0.0565
Epoch 8/25
50/50 [==============================] - 10s 192ms/step - loss: 5.4871 - acc: 0.0618
Epoch 9/25
50/50 [==============================] - 10s 190ms/step - loss: 5.4879 - acc: 0.0631
Epoch 10/25
50/50 [==============================] - 10s 192ms/step - loss: 5.4788 - acc: 0.

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 2-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>1: train=0.006544 test=0.009212
Epoch 1/25
50/50 [==============================] - 18s 361ms/step - loss: 5.8848 - acc: 0.0509
Epoch 2/25
50/50 [==============================] - 9s 189ms/step - loss: 5.5737 - acc: 0.0569
Epoch 3/25
50/50 [==============================] - 10s 192ms/step - loss: 5.6002 - acc: 0.0603
Epoch 4/25
50/50 [==============================] - 10s 193ms/step - loss: 5.5582 - acc: 0.0590
Epoch 5/25
50/50 [==============================] - 10s 191ms/step - loss: 5.5231 - acc: 0.0591
Epoch 6/25
50/50 [==============================] - 10s 196ms/step - loss: 5.5100 - acc: 0.0605
Epoch 7/25
50/50 [==============================] - 10s 193ms/step - loss: 5.5065 - acc: 0.0592
Epoch 8/25
50/50 [==============================] - 9s 190ms/step - loss: 5.4968 - acc: 0.0570
Epoch 9/25
50/50 [==============================] - 10s 191ms/step - loss: 5.4854 - acc: 0.0617
Epoch 10/25
50/50 [==============================] - 10s 192ms/step - loss: 5.4855 - acc: 0.0617
Epoch 11

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 2-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>2: train=0.000411 test=0.000570
Epoch 1/25
50/50 [==============================] - 19s 376ms/step - loss: 5.8674 - acc: 0.0542
Epoch 2/25
50/50 [==============================] - 10s 197ms/step - loss: 5.5781 - acc: 0.0593
Epoch 3/25
50/50 [==============================] - 10s 194ms/step - loss: 5.5761 - acc: 0.0581
Epoch 4/25
50/50 [==============================] - 10s 195ms/step - loss: 5.5529 - acc: 0.0605
Epoch 5/25
50/50 [==============================] - 10s 193ms/step - loss: 5.5226 - acc: 0.0614
Epoch 6/25
50/50 [==============================] - 10s 193ms/step - loss: 5.5113 - acc: 0.0595
Epoch 7/25
50/50 [==============================] - 10s 195ms/step - loss: 5.5010 - acc: 0.0578
Epoch 8/25
50/50 [==============================] - 10s 192ms/step - loss: 5.4898 - acc: 0.0575
Epoch 9/25
50/50 [==============================] - 10s 193ms/step - loss: 5.4974 - acc: 0.0581
Epoch 10/25
50/50 [==============================] - 10s 198ms/step - loss: 5.4818 - acc: 0.0610
Epoch 

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 2-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>3: train=0.003616 test=0.015353
          train      test
count  3.000000  3.000000
mean   0.003523  0.008378
std    0.003068  0.007427
min    0.000411  0.000570
25%    0.002013  0.004891
50%    0.003616  0.009212
75%    0.005080  0.012282
max    0.006544  0.015353


### Modelo de lenguaje

El modelo de lenguaje es la parte del modelo que aprende las palabras (decoder).

#### size_sm_lang_model

Vamos a ver que efecto tiene disminuir las neuronas  de la LSTM y la capa densa a la mitad.

In [48]:
# define the captioning model
def define_model(vocab_size, max_length):
	# feature extractor (encoder)
    inputs1 = Input(shape=(7, 7, 512))
    fe1 = GlobalMaxPooling2D()(inputs1)
    fe2 = Dense(128, activation='relu')(fe1)
    fe3 = RepeatVector(max_length)(fe2)
	# embedding
    inputs2 = Input(shape=(max_length,))
    emb2 = Embedding(vocab_size, 50, mask_zero=True)(inputs2)
    emb3 = LSTM(256, return_sequences=True)(emb2)
    emb4 = TimeDistributed(Dense(128, activation='relu'))(emb3)
	# merge inputs
    merged = concatenate([fe3, emb4])
	# language model (decoder)
	
    # estas
    lm2 = LSTM(256)(merged)
    lm3 = Dense(256, activation='relu')(lm2)
	
  
    outputs = Dense(vocab_size, activation='softmax')(lm3)
	# tie it together [image, seq] [word]
    model = Model(inputs=[inputs1, inputs2], outputs=outputs)
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model
 



# prepare tokenizer
tokenizer = create_tokenizer(train_descriptions)
vocab_size = len(tokenizer.word_index) + 1
print('Vocabulary Size: %d' % vocab_size)
# determine the maximum sequence length
max_length = max(len(s.split()) for s in list(train_descriptions.values()))
print('Description Length: %d' % max_length)
 
# define experiment
model_name = 'size_sm_lang_model'
verbose = 1
n_epochs = 25
n_photos_per_update = 2
n_batches_per_epoch = int(len(train) / n_photos_per_update)
n_repeats = 3
 
# run experiment
train_results, test_results = list(), list()
for i in range(n_repeats):
	# define the model
	model = define_model(vocab_size, max_length)
	# fit model
	model.fit_generator(data_generator(train_descriptions, train_features, tokenizer, max_length, n_photos_per_update), steps_per_epoch=n_batches_per_epoch, epochs=n_epochs, verbose=verbose)
	# evaluate model on training data
	train_score = evaluate_model(model, train_descriptions, train_features, tokenizer, max_length)
	test_score = evaluate_model(model, test_descriptions, test_features, tokenizer, max_length)
	# store
	train_results.append(train_score)
	test_results.append(test_score)
	print('>%d: train=%f test=%f' % ((i+1), train_score, test_score))
# save results to file
df = DataFrame()
df['train'] = train_results
df['test'] = test_results
print(df.describe())
df.to_csv(model_name+'.csv', index=False)

Vocabulary Size: 591
Description Length: 35
Epoch 1/25
50/50 [==============================] - 20s 407ms/step - loss: 5.9324 - acc: 0.0493
Epoch 2/25
50/50 [==============================] - 10s 195ms/step - loss: 5.5487 - acc: 0.0558
Epoch 3/25
50/50 [==============================] - 10s 196ms/step - loss: 5.5278 - acc: 0.0597
Epoch 4/25
50/50 [==============================] - 10s 196ms/step - loss: 5.5063 - acc: 0.0593
Epoch 5/25
50/50 [==============================] - 10s 192ms/step - loss: 5.5015 - acc: 0.0593
Epoch 6/25
50/50 [==============================] - 9s 190ms/step - loss: 5.4960 - acc: 0.0594
Epoch 7/25
50/50 [==============================] - 10s 191ms/step - loss: 5.4910 - acc: 0.0604
Epoch 8/25
50/50 [==============================] - 10s 192ms/step - loss: 5.4930 - acc: 0.0609
Epoch 9/25
50/50 [==============================] - 10s 191ms/step - loss: 5.4944 - acc: 0.0617
Epoch 10/25
50/50 [==============================] - 10s 192ms/step - loss: 5.4834 - acc: 0.0

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 2-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>1: train=0.000361 test=0.000570
Epoch 1/25
50/50 [==============================] - 19s 385ms/step - loss: 5.9473 - acc: 0.0528
Epoch 2/25
50/50 [==============================] - 10s 193ms/step - loss: 5.5473 - acc: 0.0609
Epoch 3/25
50/50 [==============================] - 10s 193ms/step - loss: 5.5272 - acc: 0.0613
Epoch 4/25
50/50 [==============================] - 10s 193ms/step - loss: 5.5041 - acc: 0.0628
Epoch 5/25
50/50 [==============================] - 10s 192ms/step - loss: 5.4946 - acc: 0.0593
Epoch 6/25
50/50 [==============================] - 10s 193ms/step - loss: 5.4873 - acc: 0.0617
Epoch 7/25
50/50 [==============================] - 10s 193ms/step - loss: 5.4897 - acc: 0.0617
Epoch 8/25
50/50 [==============================] - 10s 193ms/step - loss: 5.4769 - acc: 0.0617
Epoch 9/25
50/50 [==============================] - 10s 192ms/step - loss: 5.4735 - acc: 0.0617
Epoch 10/25
50/50 [==============================] - 10s 193ms/step - loss: 5.4758 - acc: 0.0620
Epoch 

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 2-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>2: train=0.000346 test=0.000670
Epoch 1/25
50/50 [==============================] - 20s 398ms/step - loss: 5.9623 - acc: 0.0471
Epoch 2/25
50/50 [==============================] - 10s 194ms/step - loss: 5.5478 - acc: 0.0573
Epoch 3/25
50/50 [==============================] - 10s 195ms/step - loss: 5.5379 - acc: 0.0611
Epoch 4/25
50/50 [==============================] - 10s 195ms/step - loss: 5.5196 - acc: 0.0607
Epoch 5/25
50/50 [==============================] - 10s 194ms/step - loss: 5.5024 - acc: 0.0593
Epoch 6/25
50/50 [==============================] - 10s 195ms/step - loss: 5.4913 - acc: 0.0599
Epoch 7/25
50/50 [==============================] - 10s 192ms/step - loss: 5.4816 - acc: 0.0624
Epoch 8/25
50/50 [==============================] - 10s 191ms/step - loss: 5.4788 - acc: 0.0624
Epoch 9/25
50/50 [==============================] - 10s 192ms/step - loss: 5.4796 - acc: 0.0607
Epoch 10/25
50/50 [==============================] - 10s 196ms/step - loss: 5.4788 - acc: 0.0611
Epoch 

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 3-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>3: train=0.003413 test=0.004386
          train      test
count  3.000000  3.000000
mean   0.001373  0.001876
std    0.001767  0.002175
min    0.000346  0.000570
25%    0.000353  0.000620
50%    0.000361  0.000670
75%    0.001887  0.002528
max    0.003413  0.004386


#### size_lg_lang_model

Y ahora añadimos una segunda capa al LSTM

In [49]:
# define the captioning model
def define_model(vocab_size, max_length):
	# feature extractor (encoder)
    inputs1 = Input(shape=(7, 7, 512))
    fe1 = GlobalMaxPooling2D()(inputs1)
    fe2 = Dense(128, activation='relu')(fe1)
    fe3 = RepeatVector(max_length)(fe2)
	# embedding
    inputs2 = Input(shape=(max_length,))
    emb2 = Embedding(vocab_size, 50, mask_zero=True)(inputs2)
    emb3 = LSTM(256, return_sequences=True)(emb2)
    emb4 = TimeDistributed(Dense(128, activation='relu'))(emb3)
	# merge inputs
    merged = concatenate([fe3, emb4])
	# language model (decoder)
    lm2 = LSTM(500, return_sequences=True)(merged)
    lm3 = LSTM(500)(lm2)
    lm4 = Dense(500, activation='relu')(lm3)
    outputs = Dense(vocab_size, activation='softmax')(lm4)
	# tie it together [image, seq] [word]
    model = Model(inputs=[inputs1, inputs2], outputs=outputs)
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model
 
# prepare tokenizer
tokenizer = create_tokenizer(train_descriptions)
vocab_size = len(tokenizer.word_index) + 1
print('Vocabulary Size: %d' % vocab_size)
# determine the maximum sequence length
max_length = max(len(s.split()) for s in list(train_descriptions.values()))
print('Description Length: %d' % max_length)
 
# define experiment
model_name = 'size_lg_lang_model'
verbose = 1
n_epochs = 25
n_photos_per_update = 2
n_batches_per_epoch = int(len(train) / n_photos_per_update)
n_repeats = 3
 
# run experiment
train_results, test_results = list(), list()
for i in range(n_repeats):
	# define the model
	model = define_model(vocab_size, max_length)
	# fit model
	model.fit_generator(data_generator(train_descriptions, train_features, tokenizer, max_length, n_photos_per_update), steps_per_epoch=n_batches_per_epoch, epochs=n_epochs, verbose=verbose)
	# evaluate model on training data
	train_score = evaluate_model(model, train_descriptions, train_features, tokenizer, max_length)
	test_score = evaluate_model(model, test_descriptions, test_features, tokenizer, max_length)
	# store
	train_results.append(train_score)
	test_results.append(test_score)
	print('>%d: train=%f test=%f' % ((i+1), train_score, test_score))
# save results to file
df = DataFrame()
df['train'] = train_results
df['test'] = test_results
print(df.describe())
df.to_csv(model_name+'.csv', index=False)

Vocabulary Size: 591
Description Length: 35
Epoch 1/25
50/50 [==============================] - 26s 514ms/step - loss: 5.8897 - acc: 0.0670
Epoch 2/25
50/50 [==============================] - 14s 282ms/step - loss: 5.4655 - acc: 0.0819
Epoch 3/25
50/50 [==============================] - 14s 280ms/step - loss: 5.3498 - acc: 0.0801
Epoch 4/25
50/50 [==============================] - 14s 280ms/step - loss: 5.3532 - acc: 0.0862
Epoch 5/25
50/50 [==============================] - 14s 281ms/step - loss: 5.3709 - acc: 0.0848
Epoch 6/25
50/50 [==============================] - 14s 281ms/step - loss: 5.2861 - acc: 0.0893
Epoch 7/25
50/50 [==============================] - 14s 279ms/step - loss: 5.2195 - acc: 0.0929
Epoch 8/25
50/50 [==============================] - 14s 281ms/step - loss: 5.1689 - acc: 0.0919
Epoch 9/25
50/50 [==============================] - 14s 281ms/step - loss: 5.1129 - acc: 0.0907
Epoch 10/25
50/50 [==============================] - 14s 278ms/step - loss: 5.0765 - acc: 0.

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 4-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>1: train=0.027494 test=0.032987
Epoch 1/25
50/50 [==============================] - 26s 523ms/step - loss: 5.8781 - acc: 0.0642
Epoch 2/25
50/50 [==============================] - 14s 281ms/step - loss: 5.4325 - acc: 0.0857
Epoch 3/25
50/50 [==============================] - 14s 280ms/step - loss: 5.3173 - acc: 0.0739
Epoch 4/25
50/50 [==============================] - 14s 279ms/step - loss: 5.3150 - acc: 0.0892
Epoch 5/25
50/50 [==============================] - 14s 283ms/step - loss: 5.2901 - acc: 0.0867
Epoch 6/25
50/50 [==============================] - 14s 278ms/step - loss: 5.2580 - acc: 0.0956
Epoch 7/25
50/50 [==============================] - 14s 277ms/step - loss: 5.1860 - acc: 0.0908
Epoch 8/25
50/50 [==============================] - 14s 279ms/step - loss: 5.1238 - acc: 0.0895
Epoch 9/25
50/50 [==============================] - 14s 280ms/step - loss: 5.0647 - acc: 0.0935
Epoch 10/25
50/50 [==============================] - 14s 278ms/step - loss: 5.0526 - acc: 0.0908
Epoch 

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 4-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>2: train=0.055735 test=0.047379
Epoch 1/25
50/50 [==============================] - 27s 541ms/step - loss: 5.8842 - acc: 0.0625
Epoch 2/25
50/50 [==============================] - 14s 279ms/step - loss: 5.5241 - acc: 0.0712
Epoch 3/25
50/50 [==============================] - 14s 279ms/step - loss: 5.3871 - acc: 0.0795
Epoch 4/25
50/50 [==============================] - 14s 278ms/step - loss: 5.2812 - acc: 0.0788
Epoch 5/25
50/50 [==============================] - 14s 277ms/step - loss: 5.2461 - acc: 0.0868
Epoch 6/25
50/50 [==============================] - 14s 281ms/step - loss: 5.2961 - acc: 0.0780
Epoch 7/25
50/50 [==============================] - 14s 278ms/step - loss: 5.3150 - acc: 0.0839
Epoch 8/25
50/50 [==============================] - 14s 275ms/step - loss: 5.3107 - acc: 0.0891
Epoch 9/25
50/50 [==============================] - 14s 276ms/step - loss: 5.2429 - acc: 0.0855
Epoch 10/25
50/50 [==============================] - 14s 277ms/step - loss: 5.1677 - acc: 0.0902
Epoch 

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 4-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>3: train=0.049760 test=0.042895
          train      test
count  3.000000  3.000000
mean   0.044330  0.041087
std    0.014883  0.007365
min    0.027494  0.032987
25%    0.038627  0.037941
50%    0.049760  0.042895
75%    0.052748  0.045137
max    0.055735  0.047379


### Extractor de caracteristicas

El modelo base elimina parte del modelo VGG (quedandose sólo con el principio del mismo, y añadiendo una capa de global max pooling que luego alimenta a nuestro modelo)

Vamos a realizar cambios en este paso

#### fe_avg_pool

Cambiando el Global Max Pooling a Global Average Pooling

In [50]:
from keras.layers.pooling import GlobalAveragePooling2D


# define the captioning model
def define_model(vocab_size, max_length):
	# feature extractor (encoder)
    inputs1 = Input(shape=(7, 7, 512))
    fe1 = GlobalAveragePooling2D()(inputs1)
    fe2 = Dense(128, activation='relu')(fe1)
    fe3 = RepeatVector(max_length)(fe2)
	# embedding
    inputs2 = Input(shape=(max_length,))
    emb2 = Embedding(vocab_size, 50, mask_zero=True)(inputs2)
    emb3 = LSTM(256, return_sequences=True)(emb2)
    emb4 = TimeDistributed(Dense(128, activation='relu'))(emb3)
	# merge inputs
    merged = concatenate([fe3, emb4])
	# language model (decoder)
    lm2 = LSTM(500)(merged)
    lm3 = Dense(500, activation='relu')(lm2)
    outputs = Dense(vocab_size, activation='softmax')(lm3)
	# tie it together [image, seq] [word]
    model = Model(inputs=[inputs1, inputs2], outputs=outputs)
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model




# prepare tokenizer
tokenizer = create_tokenizer(train_descriptions)
vocab_size = len(tokenizer.word_index) + 1
print('Vocabulary Size: %d' % vocab_size)
# determine the maximum sequence length
max_length = max(len(s.split()) for s in list(train_descriptions.values()))
print('Description Length: %d' % max_length)
 
# define experiment
model_name = 'fe_avg_pool'
verbose = 1
n_epochs = 25
n_photos_per_update = 2
n_batches_per_epoch = int(len(train) / n_photos_per_update)
n_repeats = 3
 
# run experiment
train_results, test_results = list(), list()
for i in range(n_repeats):
	# define the model
	model = define_model(vocab_size, max_length)
	# fit model
	model.fit_generator(data_generator(train_descriptions, train_features, tokenizer, max_length, n_photos_per_update), steps_per_epoch=n_batches_per_epoch, epochs=n_epochs, verbose=verbose)
	# evaluate model on training data
	train_score = evaluate_model(model, train_descriptions, train_features, tokenizer, max_length)
	test_score = evaluate_model(model, test_descriptions, test_features, tokenizer, max_length)
	# store
	train_results.append(train_score)
	test_results.append(test_score)
	print('>%d: train=%f test=%f' % ((i+1), train_score, test_score))
# save results to file
df = DataFrame()
df['train'] = train_results
df['test'] = test_results
print(df.describe())
df.to_csv(model_name+'.csv', index=False)

Vocabulary Size: 591
Description Length: 35
Epoch 1/25
50/50 [==============================] - 22s 445ms/step - loss: 5.8725 - acc: 0.0486
Epoch 2/25
50/50 [==============================] - 10s 195ms/step - loss: 5.5662 - acc: 0.0659
Epoch 3/25
50/50 [==============================] - 10s 194ms/step - loss: 5.4638 - acc: 0.0833
Epoch 4/25
50/50 [==============================] - 10s 195ms/step - loss: 5.3684 - acc: 0.0929
Epoch 5/25
50/50 [==============================] - 10s 197ms/step - loss: 5.2308 - acc: 0.0978
Epoch 6/25
50/50 [==============================] - 10s 193ms/step - loss: 5.1369 - acc: 0.0973
Epoch 7/25
50/50 [==============================] - 10s 196ms/step - loss: 5.0574 - acc: 0.1000
Epoch 8/25
50/50 [==============================] - 10s 192ms/step - loss: 5.0009 - acc: 0.1016
Epoch 9/25
50/50 [==============================] - 10s 191ms/step - loss: 4.9013 - acc: 0.1057
Epoch 10/25
50/50 [==============================] - 10s 192ms/step - loss: 4.7244 - acc: 0.

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 3-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>1: train=0.068819 test=0.139216
Epoch 1/25
50/50 [==============================] - 22s 450ms/step - loss: 5.8724 - acc: 0.0557
Epoch 2/25
50/50 [==============================] - 10s 192ms/step - loss: 5.4910 - acc: 0.0698
Epoch 3/25
50/50 [==============================] - 10s 196ms/step - loss: 5.3711 - acc: 0.0879
Epoch 4/25
50/50 [==============================] - 10s 196ms/step - loss: 5.2256 - acc: 0.0924
Epoch 5/25
50/50 [==============================] - 10s 193ms/step - loss: 5.0689 - acc: 0.0953
Epoch 6/25
50/50 [==============================] - 10s 193ms/step - loss: 4.9026 - acc: 0.0989
Epoch 7/25
50/50 [==============================] - 10s 194ms/step - loss: 4.7003 - acc: 0.1057
Epoch 8/25
50/50 [==============================] - 10s 192ms/step - loss: 4.5434 - acc: 0.1085
Epoch 9/25
50/50 [==============================] - 10s 193ms/step - loss: 4.4362 - acc: 0.1120
Epoch 10/25
50/50 [==============================] - 10s 191ms/step - loss: 4.2886 - acc: 0.1159
Epoch 

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 4-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>2: train=0.117968 test=0.037236
Epoch 1/25
50/50 [==============================] - 24s 479ms/step - loss: 5.8567 - acc: 0.0569
Epoch 2/25
50/50 [==============================] - 10s 199ms/step - loss: 5.5120 - acc: 0.0729
Epoch 3/25
50/50 [==============================] - 10s 198ms/step - loss: 5.3921 - acc: 0.0875
Epoch 4/25
50/50 [==============================] - 10s 197ms/step - loss: 5.2799 - acc: 0.0855
Epoch 5/25
50/50 [==============================] - 10s 196ms/step - loss: 5.1431 - acc: 0.0900
Epoch 6/25
50/50 [==============================] - 10s 196ms/step - loss: 5.0161 - acc: 0.0974
Epoch 7/25
50/50 [==============================] - 10s 199ms/step - loss: 4.8947 - acc: 0.1017
Epoch 8/25
50/50 [==============================] - 10s 198ms/step - loss: 4.8294 - acc: 0.1058
Epoch 9/25
50/50 [==============================] - 10s 195ms/step - loss: 4.6982 - acc: 0.1021
Epoch 10/25
50/50 [==============================] - 10s 195ms/step - loss: 4.5241 - acc: 0.1124
Epoch 

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 3-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


#### fe_flat

Y quitando el Pooling

In [51]:
# define the captioning model
def define_model(vocab_size, max_length):
	# feature extractor (encoder)
    inputs1 = Input(shape=(7, 7, 512))
    fe1 = Flatten()(inputs1)
    fe2 = Dense(128, activation='relu')(fe1)
    fe3 = RepeatVector(max_length)(fe2)
	# embedding
    inputs2 = Input(shape=(max_length,))
    emb2 = Embedding(vocab_size, 50, mask_zero=True)(inputs2)
    emb3 = LSTM(256, return_sequences=True)(emb2)
    emb4 = TimeDistributed(Dense(128, activation='relu'))(emb3)
	# merge inputs
    merged = concatenate([fe3, emb4])
	# language model (decoder)
    lm2 = LSTM(500)(merged)
    lm3 = Dense(500, activation='relu')(lm2)
    outputs = Dense(vocab_size, activation='softmax')(lm3)
	# tie it together [image, seq] [word]
    model = Model(inputs=[inputs1, inputs2], outputs=outputs)
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model

# prepare tokenizer
tokenizer = create_tokenizer(train_descriptions)
vocab_size = len(tokenizer.word_index) + 1
print('Vocabulary Size: %d' % vocab_size)
# determine the maximum sequence length
max_length = max(len(s.split()) for s in list(train_descriptions.values()))
print('Description Length: %d' % max_length)
 
# define experiment
model_name = 'fe_flat'
verbose = 1
n_epochs = 25
n_photos_per_update = 2
n_batches_per_epoch = int(len(train) / n_photos_per_update)
n_repeats = 3
 
# run experiment
train_results, test_results = list(), list()
for i in range(n_repeats):
	# define the model
	model = define_model(vocab_size, max_length)
	# fit model
	model.fit_generator(data_generator(train_descriptions, train_features, tokenizer, max_length, n_photos_per_update), steps_per_epoch=n_batches_per_epoch, epochs=n_epochs, verbose=verbose)
	# evaluate model on training data
	train_score = evaluate_model(model, train_descriptions, train_features, tokenizer, max_length)
	test_score = evaluate_model(model, test_descriptions, test_features, tokenizer, max_length)
	# store
	train_results.append(train_score)
	test_results.append(test_score)
	print('>%d: train=%f test=%f' % ((i+1), train_score, test_score))
# save results to file
df = DataFrame()
df['train'] = train_results
df['test'] = test_results
print(df.describe())
df.to_csv(model_name+'.csv', index=False)

Vocabulary Size: 591
Description Length: 35
Epoch 1/25
50/50 [==============================] - 24s 484ms/step - loss: 5.8780 - acc: 0.0526
Epoch 2/25
50/50 [==============================] - 10s 202ms/step - loss: 5.5738 - acc: 0.0560
Epoch 3/25
50/50 [==============================] - 10s 201ms/step - loss: 5.5695 - acc: 0.0573
Epoch 4/25
50/50 [==============================] - 10s 201ms/step - loss: 5.5198 - acc: 0.0583
Epoch 5/25
50/50 [==============================] - 10s 201ms/step - loss: 5.4870 - acc: 0.0601
Epoch 6/25
50/50 [==============================] - 10s 200ms/step - loss: 5.4557 - acc: 0.0612
Epoch 7/25
50/50 [==============================] - 10s 195ms/step - loss: 5.4206 - acc: 0.0625
Epoch 8/25
50/50 [==============================] - 10s 197ms/step - loss: 5.3726 - acc: 0.0606
Epoch 9/25
50/50 [==============================] - 10s 198ms/step - loss: 5.2957 - acc: 0.0644
Epoch 10/25
50/50 [==============================] - 10s 200ms/step - loss: 5.2229 - acc: 0.

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 3-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>1: train=0.132634 test=0.082226
Epoch 1/25
50/50 [==============================] - 24s 487ms/step - loss: 5.8830 - acc: 0.0527
Epoch 2/25
50/50 [==============================] - 10s 202ms/step - loss: 5.5882 - acc: 0.0574
Epoch 3/25
50/50 [==============================] - 10s 201ms/step - loss: 5.5423 - acc: 0.0600
Epoch 4/25
50/50 [==============================] - 10s 200ms/step - loss: 5.5239 - acc: 0.0573
Epoch 5/25
50/50 [==============================] - 10s 202ms/step - loss: 5.4734 - acc: 0.0588
Epoch 6/25
50/50 [==============================] - 10s 199ms/step - loss: 5.4170 - acc: 0.0612
Epoch 7/25
50/50 [==============================] - 10s 200ms/step - loss: 5.3526 - acc: 0.0592
Epoch 8/25
50/50 [==============================] - 10s 201ms/step - loss: 5.2582 - acc: 0.0651
Epoch 9/25
50/50 [==============================] - 10s 200ms/step - loss: 5.1577 - acc: 0.0642
Epoch 10/25
50/50 [==============================] - 10s 199ms/step - loss: 5.0550 - acc: 0.0644
Epoch 

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 4-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)
/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 3-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>2: train=0.017271 test=0.104119
Epoch 1/25
50/50 [==============================] - 25s 508ms/step - loss: 5.8781 - acc: 0.0511
Epoch 2/25
50/50 [==============================] - 10s 204ms/step - loss: 5.5501 - acc: 0.0568
Epoch 3/25
50/50 [==============================] - 10s 202ms/step - loss: 5.4925 - acc: 0.0599
Epoch 4/25
50/50 [==============================] - 10s 195ms/step - loss: 5.4533 - acc: 0.0590
Epoch 5/25
50/50 [==============================] - 10s 198ms/step - loss: 5.3810 - acc: 0.0615
Epoch 6/25
50/50 [==============================] - 10s 196ms/step - loss: 5.2470 - acc: 0.0628
Epoch 7/25
50/50 [==============================] - 10s 198ms/step - loss: 5.1210 - acc: 0.0644
Epoch 8/25
50/50 [==============================] - 10s 199ms/step - loss: 4.9615 - acc: 0.0624
Epoch 9/25
50/50 [==============================] - 10s 200ms/step - loss: 4.8805 - acc: 0.0632
Epoch 10/25
50/50 [==============================] - 10s 200ms/step - loss: 4.6180 - acc: 0.0707
Epoch 

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 3-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


>3: train=0.136263 test=0.101933
          train      test
count  3.000000  3.000000
mean   0.095389  0.096093
std    0.067677  0.012058
min    0.017271  0.082226
25%    0.074952  0.092080
50%    0.132634  0.101933
75%    0.134449  0.103026
max    0.136263  0.104119


## Evaluación

Tras todos estos experimentos vemos que:

In [0]:
files_in_directory = listdir('/content')

# Generamos una lista con todos los archivos CSV que hay en el directorio

csv_files = list()

for f in files_in_directory:
  try:
    csv_e = f.split('.')[1]
  except IndexError:
    csv_e = ''
  if csv_e == 'csv':
    csv_files.append(f)

In [0]:
import pandas as pd

In [0]:
# unimos todos los CSV y lo guardamos todo en models-results.csv

todos = pd.DataFrame(columns=['train','test','model'])
# agregamos todos los resultados en un dataframe con los resultados de train 
# y test y el nombre delmodelo

for f in csv_files:
    data = pd.read_csv(f, index_col=None, header=0)
    data['model'] = f
    todos = pd.concat([todos, data])
    
todos.reindex()
todos.to_csv('models-results.csv')

In [0]:
# Calculamos la media de cada experimento y lo guardamos todo en 
# models-summary.csv

li= []
med = []

# agregamos todos los resultados en un dataframe con los resultados de train 
# y test y el nombre del modelo

for f in csv_files:
    data = pd.read_csv(f, index_col=None, header=0)
    data['model'] = f
    medias = data.mean()
    linea = [medias[0],medias[1],f]
    
    li.append(data)
    med.append(linea)
  
  
modelos = pd.concat(li, axis=0, ignore_index=True)

medias = pd.DataFrame(med, columns=['train','test','model'])

In [0]:
medias.to_csv('models-summary.csv', index=False)

In [55]:
medias.sort_values(by=['train', 'test'])

train      test                   model
2  0.000346  0.000570           baseline1.csv
9  0.001327  0.001816   size_sm_seq_model.csv
7  0.001373  0.001876  size_sm_lang_model.csv
0  0.002208  0.003412   size_lg_seq_model.csv
5  0.002391  0.003111   size_lg_fixed_vec.csv
3  0.003523  0.008378   size_em_seq_model.csv
8  0.044330  0.041087  size_lg_lang_model.csv
4  0.070102  0.057846   size_sm_fixed_vec.csv
6  0.088770  0.116737         fe_avg_pool.csv
1  0.095389  0.096093             fe_flat.csv

Respecto a la linea base, vemos que las siguientes modificaciones han mejoran el rendimiento:

* size_lg_lang_model
* fe_avg_pool
* size_lg_seq_model
* size_sm_fixed_model

Así pues, definimos un modelo que incorpore las mejoras que hemos encontrado en los experimentos.


## Entrenamiento con más datos

![modelo](https://docs.google.com/drawings/d/e/2PACX-1vQend4dewDH4a9ZRlRVDjmbUokgp8COGpo__TN3_Ye4Wlf0bvJhN8REwjXeVFj_-lC2isskBFAnJTqm/pub?w=846&h=345)

In [0]:
from keras.layers.pooling import GlobalAveragePooling2D

# define the captioning model
def define_model(vocab_size, max_length):
	# feature extractor (encoder)
    inputs1 = Input(shape=(7, 7, 512))
    fe1 = GlobalAveragePooling2D()(inputs1)
    fe2 = Dense(128, activation='relu')(fe1)
    fe3 = RepeatVector(max_length)(fe2)
	# embedding
    inputs2 = Input(shape=(max_length,))
    emb2 = Embedding(vocab_size, 50, mask_zero=True)(inputs2)
    emb3 = LSTM(256, return_sequences=True)(emb2)
    emb4 = TimeDistributed(Dense(128, activation='relu'))(emb3)
    
    # merge inputs
    merged = concatenate([fe3, emb4])
	# language model (decoder)
    lm2 = LSTM(500, return_sequences=True)(merged)
    lm3 = LSTM(500)(lm2)
    lm4 = Dense(500, activation='relu')(lm3)
    outputs = Dense(vocab_size, activation='softmax')(lm3)
	# tie it together [image, seq] [word]
    model = Model(inputs=[inputs1, inputs2], outputs=outputs)
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model

In [57]:
filename = 'train-test-val-set.txt'
dataset = load_set(filename)
print('Dataset: %d' % len(dataset))

# train-test split
train, test, val = train_test_split(dataset,50,10,5)
print (val)
print('Train=%d, Test=%d' % (len(train), len(test)))
# descriptions
train_descriptions = load_clean_descriptions('descriptions.txt', train)
test_descriptions = load_clean_descriptions('descriptions.txt', test)
val_descriptions = load_clean_descriptions('descriptions.txt', val)

print('Descriptions: train=%d, test=%d, val=%d' % (len(train_descriptions), 
                                                    len(test_descriptions), 
                                                    len(val_descriptions)))
# photo features
train_features = load_photo_features('features.pkl', train)
test_features = load_photo_features('features.pkl', test)
val_features = load_photo_features('features.pkl', val)

print('Photos: train=%d, test=%d, val=%d' % (len(train_features), 
                                             len(test_features),
                                             len(val_features)))

Dataset: 1000
{'4438301773', '4412893298', '4521610802', '454333157', '4403629017', '4407494664', '442138526', '4431086360', '4552389008', '446902008', '4441843357', '441921713', '4481066026', '4458984161', '4544052868', '455914518', '4548074929', '4488485439', '451547131', '435739506', '4519904608', '4544246166', '4561823639', '4443934130', '4523882717', '4538960982', '43390068', '4473229124', '4463211241', '4496551407', '4545104306', '4433557295', '4477683613', '437057062', '4503067869', '4467161305', '4556114229', '439830368', '4351426633', '4475974227', '4363060125', '4463772847', '4369970740', '4558179720', '4533955542', '4450184997', '4493330346', '4497873178', '4459992117', '4493008657'}
Train=500, Test=100
Descriptions: train=500, test=100, val=50
Photos: train=500, test=100, val=50


In [58]:
# prepare tokenizer
tokenizer = create_tokenizer(train_descriptions)
vocab_size = len(tokenizer.word_index) + 1
print('Vocabulary Size: %d' % vocab_size)
# determine the maximum sequence length
max_length = max(len(s.split()) for s in list(train_descriptions.values()))
print('Description Length: %d' % max_length)
 
  
verbose = 1
n_epochs = 50
n_photos_per_update = 4
n_batches_per_epoch = int(len(train) / n_photos_per_update)


# run experiment
train_results, test_results = list(), list()

# define the model
model = define_model(vocab_size, max_length)

# fit model
model.fit_generator(data_generator(train_descriptions, train_features, tokenizer, max_length, n_photos_per_update), steps_per_epoch=n_batches_per_epoch, epochs=n_epochs, verbose=verbose)



Vocabulary Size: 1542
Description Length: 36
Epoch 1/50
125/125 [==============================] - 55s 440ms/step - loss: 6.0648 - acc: 0.0738
Epoch 2/50
125/125 [==============================] - 38s 305ms/step - loss: 5.6279 - acc: 0.0957
Epoch 3/50
125/125 [==============================] - 38s 306ms/step - loss: 5.4814 - acc: 0.1025
Epoch 4/50
125/125 [==============================] - 38s 306ms/step - loss: 5.2987 - acc: 0.1054
Epoch 5/50
125/125 [==============================] - 38s 307ms/step - loss: 5.2124 - acc: 0.1060
Epoch 6/50
125/125 [==============================] - 39s 308ms/step - loss: 5.1314 - acc: 0.1106
Epoch 7/50
125/125 [==============================] - 38s 307ms/step - loss: 5.0484 - acc: 0.1136
Epoch 8/50
125/125 [==============================] - 38s 307ms/step - loss: 4.9589 - acc: 0.1195
Epoch 9/50
125/125 [==============================] - 38s 306ms/step - loss: 4.8805 - acc: 0.1213
Epoch 10/50
125/125 [==============================] - 38s 305ms/step - l

## Evaluacion final

In [0]:
def evaluate_model(model, descriptions, photos, tokenizer, max_length):
	actual, predicted = list(), list()
	# step over the whole set
	for key, desc in descriptions.items():
		# generate description
		yhat = generate_desc(model, tokenizer, photos[key], max_length)
		# store actual and predicted
		actual.append([desc.split()])
		predicted.append(yhat.split())
		print('Actual:    %s' % desc)
		print('Predicted: %s' % yhat)
		if len(actual) >= 5:
			break
	# calculate BLEU score
	bleu = corpus_bleu(actual, predicted)
	return bleu

In [65]:
# evaluate model on training data
train_score = evaluate_model(model, train_descriptions, train_features, tokenizer, max_length)
test_score = evaluate_model(model, test_descriptions, test_features, tokenizer, max_length)

# store
train_results.append(train_score)
test_results.append(test_score)


Actual:    startseq small girl in the grass plays with fingerpaints in front of white canvas with rainbow on it endseq
Predicted: startseq little boy in the brown tshirt is running on the snow endseq
Actual:    startseq the white out conditions of snow on the ground seem to almost obliverate the details of man dressed for the cold weather in heavy jacket and red hat riding bicycle in suburban neighborhood endseq
Predicted: startseq the white out conditions of snow on the ground seem to almost obliverate the details of man dressed for the cold weather in heavy jacket and red hat riding bicycle in suburban neighborhood endseq
Actual:    startseq person wearing skis looking at framed pictures set up in the snow endseq
Predicted: startseq person wearing skis looking on framed pictures set appears in the snow endseq
Actual:    startseq group of people stand in the back of truck filled with cotton endseq
Predicted: startseq group of people stand in the back of truck filled with cotton endseq

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 3-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


In [66]:
df = DataFrame()
df['train'] = train_results
df['test'] = test_results
print(df.describe())

df.to_csv('final_result.csv', index=False)

         train      test
count  2.00000  2.000000
mean   0.73463  0.267518
std    0.00000  0.000000
min    0.73463  0.267518
25%    0.73463  0.267518
50%    0.73463  0.267518
75%    0.73463  0.267518
max    0.73463  0.267518


## Conclusiones


Vemos unos resultados suficientemente buenos. Las frases estan bien construidas, pero claramente hay overfitting, ya que parece que nuestro modelo se ha aprendido demasiado bien el dataset. 

Aun así son resultados prometedores, y probablemente usandoo el dataset completo y ajustando algún parametro de entrenamiento de forma más fina, podremos tener un buen modelo. 

Para ello, necesitamos tiempo y máquina, pero para una primera aproximación está bien.
